In [0]:
%restart_python

In [0]:
%sql
-- Step 1: Create schema
CREATE DATABASE IF NOT EXISTS upi_fraud_schema;
USE upi_fraud_schema;

-- Step 2: Drop tables if exist (in correct order to avoid dependency issues)
DROP TABLE IF EXISTS upi_fraud_schema.transactions;
DROP TABLE IF EXISTS upi_fraud_schema.devices;
DROP TABLE IF EXISTS upi_fraud_schema.recipients;
DROP TABLE IF EXISTS upi_fraud_schema.users;

-- Step 3: Create tables with NOT NULL on PKs
CREATE TABLE users (
    user_id INT NOT NULL,
    registration_date DATE,
    default_location STRING,
    account_age_days INT,
    avg_txn_amount FLOAT,
    is_merchant BOOLEAN
) USING DELTA;

CREATE TABLE devices (
    device_id INT NOT NULL,
    user_id INT NOT NULL,
    device_type STRING,
    first_used TIMESTAMP,
    last_used TIMESTAMP
) USING DELTA;

CREATE TABLE recipients (
    recipient_id INT NOT NULL,
    recipient_type STRING,
    recipient_bank STRING,
    recipient_ifsc STRING,
    risk_score FLOAT,
    txn_volume INT
) USING DELTA;

CREATE TABLE transactions (
    transaction_id INT NOT NULL,
    user_id INT NOT NULL,
    recipient_id INT NOT NULL,
    amount FLOAT,
    timestamp TIMESTAMP,
    location STRING,
    device_id INT NOT NULL,
    channel STRING,
    txn_type STRING,
    bank_name STRING,
    bank_ifsc STRING
) USING DELTA;

-- Step 4: Add Primary Keys
ALTER TABLE users ADD CONSTRAINT pk_users PRIMARY KEY (user_id);
ALTER TABLE devices ADD CONSTRAINT pk_devices PRIMARY KEY (device_id);
ALTER TABLE recipients ADD CONSTRAINT pk_recipients PRIMARY KEY (recipient_id);
ALTER TABLE transactions ADD CONSTRAINT pk_transactions PRIMARY KEY (transaction_id);


In [0]:
%sql
-- Add foreign key from devices.user_id → users.user_id
ALTER TABLE devices ADD CONSTRAINT fk_devices_user
FOREIGN KEY (user_id)
REFERENCES users(user_id);

-- Add foreign key from transactions.user_id → users.user_id
ALTER TABLE transactions ADD CONSTRAINT fk_txn_user
FOREIGN KEY (user_id)
REFERENCES users(user_id);

-- Add foreign key from transactions.device_id → devices.device_id
ALTER TABLE transactions ADD CONSTRAINT fk_txn_device
FOREIGN KEY (device_id)
REFERENCES devices(device_id);

-- Add foreign key from transactions.recipient_id → recipients.recipient_id
ALTER TABLE transactions ADD CONSTRAINT fk_txn_recipient
FOREIGN KEY (recipient_id)
REFERENCES recipients(recipient_id);


In [0]:
%sql
SELECT 
  t.transaction_id, 
  t.amount,
  u.default_location,
  d.device_type,
  r.recipient_type
FROM transactions t
JOIN users u ON t.user_id = u.user_id
JOIN devices d ON t.device_id = d.device_id
JOIN recipients r ON t.recipient_id = r.recipient_id
LIMIT 10;


transaction_id amount default_location device_type recipient_type

In [0]:
# 📦 UPI Fraud Synthetic Data Generator – All Tables + Features (Single Cell)

from faker import Faker
from datetime import datetime, timedelta
import random
from collections import defaultdict
from pyspark.sql.functions import hour, dayofweek, col, when

fake = Faker('en_IN')
spark.sql("CREATE DATABASE IF NOT EXISTS upi_fraud_schema")
spark.sql("USE upi_fraud_schema")

# --------------------------
# CONFIG
# --------------------------
NUM_USERS = 2000
NUM_DEVICES = 1000
NUM_RECIPIENTS = 1500
NUM_TRANSACTIONS = 20000
indian_cities = ["Delhi", "Mumbai", "Bangalore", "Hyderabad", "Ahmedabad", "Chennai", "Kolkata", "Pune", "Jaipur"]
indian_banks = ["SBI", "HDFC", "ICICI", "Axis", "PNB", "BOB", "Canara", "Union Bank", "IDFC", "Kotak"]

# --------------------------
# USERS
# --------------------------
user_list = []
for i in range(NUM_USERS):
    reg_date = fake.date_between(start_date='-2y', end_date='-6m')
    age_days = (datetime.now().date() - reg_date).days
    user_list.append((i, reg_date, random.choice(indian_cities), age_days, round(random.uniform(100, 2000), 2), random.choice([True, False])))

users_df = spark.createDataFrame(user_list, schema="""
    user_id INT,
    registration_date DATE,
    default_location STRING,
    account_age_days INT,
    avg_txn_amount FLOAT,
    is_merchant BOOLEAN
""")
users_df.write.mode("overwrite").format("delta").saveAsTable("upi_fraud_schema.users")

# --------------------------
# DEVICES
# --------------------------
user_ids = [row.user_id for row in users_df.collect()]
device_list = []
user_to_devices = defaultdict(list)
for i in range(NUM_DEVICES):
    uid = random.choice(user_ids)
    first_used = fake.date_time_between(start_date='-1y', end_date='-6m')
    last_used = first_used + timedelta(days=random.randint(30, 300))
    device_list.append((i, uid, random.choice(["Android", "iOS"]), first_used, last_used))
    user_to_devices[uid].append(i)

devices_df = spark.createDataFrame(device_list, schema="""
    device_id INT,
    user_id INT,
    device_type STRING,
    first_used TIMESTAMP,
    last_used TIMESTAMP
""")
devices_df.write.mode("overwrite").format("delta").saveAsTable("upi_fraud_schema.devices")

# --------------------------
# RECIPIENTS
# --------------------------
recipient_list = []
recipient_ids = []
user_to_recipients = defaultdict(list)
for i in range(NUM_RECIPIENTS):
    recipient_list.append((i, random.choice(["merchant", "biller", "individual"]), random.choice(indian_banks), fake.bothify(text="????0#####"), round(random.uniform(0, 1), 2), random.randint(10, 1000)))
    recipient_ids.append(i)
for uid in user_ids:
    user_to_recipients[uid] = random.sample(recipient_ids, k=random.randint(1, min(35, len(recipient_ids))))

recipients_df = spark.createDataFrame(recipient_list, schema="""
    recipient_id INT,
    recipient_type STRING,
    recipient_bank STRING,
    recipient_ifsc STRING,
    risk_score FLOAT,
    txn_volume INT
""")
recipients_df.write.mode("overwrite").format("delta").saveAsTable("upi_fraud_schema.recipients")

# --------------------------
# TRANSACTIONS
# --------------------------
transaction_list = []
for i in range(NUM_TRANSACTIONS):
    uid = random.choice(user_ids)
    if not user_to_devices[uid]:
        continue  # Skip if the user has no devices
    did = random.choice(user_to_devices[uid])
    rid = random.choice(user_to_recipients[uid])
    amt = float(f"{random.uniform(50, 5000):.2f}")
    ts_date = fake.date_between(start_date='-6m', end_date='today')
    ts = datetime.combine(ts_date, datetime.min.time()) + timedelta(hours=random.randint(0, 23), minutes=random.randint(0, 59))
    transaction_list.append((
        i, uid, rid, amt, ts, random.choice(indian_cities), did,
        random.choice(["GPay", "PhonePe", "Paytm", "BHIM"]),
        random.choice(["pay", "refund", "request"]),
        random.choice(indian_banks), fake.bothify(text="????0#####")
    ))

transactions_df = spark.createDataFrame(transaction_list, schema="""
    transaction_id INT,
    user_id INT,
    recipient_id INT,
    amount FLOAT,
    timestamp TIMESTAMP,
    location STRING,
    device_id INT,
    channel STRING,
    txn_type STRING,
    bank_name STRING,
    bank_ifsc STRING
""")
transactions_df.write.mode("overwrite").format("delta").saveAsTable("upi_fraud_schema.transactions")

# --------------------------
# FEATURE TABLE
# --------------------------
features_df = transactions_df.alias("t") \
    .join(users_df.alias("u"), col("t.user_id") == col("u.user_id")) \
    .join(devices_df.alias("d"), col("t.device_id") == col("d.device_id")) \
    .join(recipients_df.alias("r"), col("t.recipient_id") == col("r.recipient_id")) \
    .withColumn("hour", hour("timestamp")) \
    .withColumn("day_of_week", dayofweek("timestamp")) \
    .withColumn("amount_deviation", col("amount") - col("avg_txn_amount")) \
    .withColumn("is_high_value", (col("amount") > 3000).cast("int")) \
    .withColumn("is_odd_hour", when((col("hour") < 6) | (col("hour") > 22), 1).otherwise(0)) \
    .select("transaction_id", "t.user_id", "t.recipient_id", "t.device_id", "amount", "hour", "day_of_week",
            "amount_deviation", "is_high_value", "is_odd_hour", "channel", "txn_type",
            "recipient_type", "device_type", "default_location", "location")

features_df.write.mode("overwrite").format("delta").saveAsTable("upi_fraud_schema.training_features")

In [0]:
%sql
-- View sample of features
SELECT 
  transaction_id, 
  user_id, 
  recipient_id, 
  device_id, 
  ROUND(amount, 2) AS amount, 
  hour, 
  day_of_week, 
  amount_deviation, 
  is_high_value, 
  is_odd_hour, 
  channel, 
  txn_type, 
  recipient_type, 
  device_type, 
  default_location, 
  location
FROM upi_fraud_schema.training_features;

transaction_id user_id recipient_id device_id amount hour day_of_week amount_deviation is_high_value is_odd_hour channel txn_type recipient_type device_type default_location location 0 51 272 325 1437.67 1 5 437.92004 0 1 Paytm refund individual null Pune Ahmedabad 1 129 587 878 4098.93 6 5 2285.6 1 0 BHIM refund merchant null Delhi Pune 2 650 1488 449 4736.51 13 5 3115.9 1 0 GPay request individual null Bangalore Ahmedabad 3 148 151 32 1267.2 20 5 1045.2799 0 0 BHIM refund merchant null Ahmedabad Chennai 4 508 836 786 1579.66 18 5 1371.0801 0 0 PhonePe request biller null Jaipur Jaipur 12 20 24 363 3962.17 6 5 2238.94 1 0 Paytm pay individual null Jaipur Pune 14 1535 812 368 2492.52 20 5 1803.37 0 0 GPay refund biller null Chennai Delhi 16 695 1003 682 4538.94 22 5 2935.27 1 0 Paytm request individual null Ahmedabad Mumbai 20 906 751 510 1665.24 17 5 131.17993 0 0 BHIM request individual null Ahmedabad Ahmedabad 21 916 1073 731 1176.64 20 5 713.04004 0 0 PhonePe refund biller null Bangalore Delhi 26 1794 1345 744 313.52 20 5 50.97998 0 0 BHIM refund individual null Ahmedabad Delhi 29 1839 1272 251 2553.99 11 5 1158.39 0 0 PhonePe refund merchant null Jaipur Bangalore 32 1194 59 245 4101.61 16 5 3674.71 1 0 BHIM request biller null Ahmedabad Bangalore 33 78 154 819 1822.89 10 5 688.88 0 0 GPay pay individual null Chennai Chennai 35 1300 1016 275 2424.22 5 5 634.13 0 1 GPay refund biller null Bangalore Hyderabad 36 1248 687 830 1203.33 6 5 210.94995 0 0 PhonePe refund individual null Bangalore Chennai 38 621 1350 487 1602.65 11 5 -290.27002 0 0 GPay pay merchant null Kolkata Pune 40 574 612 808 249.35 4 5 -991.25 0 1 Paytm refund individual null Pune Jaipur 41 42 778 395 3889.28 21 5 2618.75 1 0 PhonePe pay individual null Chennai Ahmedabad 42 1251 1205 486 3694.83 3 5 2364.96 1 1 Paytm request biller null Pune Hyderabad 43 256 878 221 4572.29 11 5 3273.07 1 0 Paytm pay individual null Hyderabad Chennai 44 704 973 393 861.47 14 5 -734.22 0 0 Paytm refund merchant null Hyderabad Delhi 46 964 1369 869 1754.78 9 5 967.52 0 0 BHIM pay biller null Kolkata Pune 49 516 549 950 2909.21 5 5 1080.84 0 1 GPay request biller null Hyderabad Bangalore 54 964 799 869 1390.25 9 5 602.99 0 0 Paytm refund biller null Kolkata Pune 57 323 859 521 2619.39 8 5 2108.7798 0 0 Paytm refund merchant null Bangalore Delhi 58 1512 559 720 4039.84 3 5 3133.73 1 1 Paytm pay biller null Jaipur Pune 59 1274 782 952 4103.05 9 5 3578.2698 1 0 Paytm request individual null Mumbai Mumbai 60 729 988 361 85.99 13 5 -619.81 0 0 Paytm request individual null Kolkata Jaipur 75 979 522 238 443.15 17 5 -198.30002 0 0 PhonePe request individual null Jaipur Chennai 76 906 751 510 3947.78 18 5 2413.72 1 0 Paytm pay individual null Ahmedabad Kolkata 77 1041 718 19 4536.87 21 5 2570.7803 1 0 GPay pay individual null Jaipur Delhi 78 1111 1408 589 345.67 15 5 28.74002 0 0 Paytm pay individual null Bangalore Kolkata 80 698 945 520 3886.12 20 5 2211.69 1 0 BHIM pay merchant null Pune Jaipur 81 1102 276 278 2177.61 1 5 668.0001 0 1 GPay pay merchant null Mumbai Bangalore 83 280 1190 342 3888.53 3 5 3607.34 1 1 PhonePe pay individual null Kolkata Chennai 90 953 361 672 4596.12 16 5 4457.27 1 0 GPay request merchant null Hyderabad Jaipur 94 1994 1076 146 4160.9 15 5 2608.7598 1 0 BHIM pay individual null Hyderabad Bangalore 95 1934 416 473 2923.46 11 5 2518.1099 0 0 PhonePe pay biller null Hyderabad Bangalore 97 538 1319 490 3846.99 2 5 2457.1 1 1 Paytm refund biller null Jaipur Bangalore 98 1714 467 858 4610.36 9 5 4184.1597 1 0 PhonePe refund merchant null Kolkata Hyderabad 99 415 1467 478 4490.4 3 5 3745.19 1 1 Paytm pay biller null Mumbai Kolkata 102 449 268 477 1220.95 7 5 -18.140015 0 0 GPay pay individual null Hyderabad Jaipur 104 1850 1055 508 4645.61 22 5 3984.8198 1 0 BHIM pay merchant null Pune Jaipur 107 188 380 85 324.28 20 5 -1374.1699 0 0 BHIM pay individual null Chennai Pune 109 682 1315 595 1565.05 12 5 -177.8999 0 0 BHIM request biller null Ahmedabad Chennai 110 51

In [0]:
from pyspark.sql.functions import col, when

# Load existing table
features_df = spark.table("upi_fraud_schema.training_features")

# Drop 'device_type'
features_df = features_df.drop("device_type")

# Add 'fraud' column based on rules without 'risk_score'
fraud_df = features_df.withColumn(
    "fraud",
    when(
        (
            (col("is_odd_hour") == 1) &
            (col("amount") > 4000) &
            (col("amount_deviation") > 1500) &
            (col("recipient_type") == "individual") &
            (col("default_location") != col("location"))
        ),
        1
    ).otherwise(0)
)

# Save updated version with schema merge enabled
fraud_df.write.mode("overwrite").format("delta") \
    .option("mergeSchema", "true") \
    .saveAsTable("upi_fraud_schema.training_features")

In [0]:
%sql
-- View sample of features
SELECT 
  transaction_id, 
  user_id, 
  recipient_id, 
  device_id, 
  ROUND(amount, 2) AS amount, 
  hour, 
  day_of_week, 
  amount_deviation, 
  is_high_value, 
  is_odd_hour, 
  channel, 
  txn_type, 
  recipient_type, 
  device_type, 
  default_location, 
  location,
  fraud
FROM upi_fraud_schema.training_features
;

transaction_id user_id recipient_id device_id amount hour day_of_week amount_deviation is_high_value is_odd_hour channel txn_type recipient_type device_type default_location location fraud 0 51 272 325 1437.67 1 5 437.92004 0 1 Paytm refund individual null Pune Ahmedabad 0 1 129 587 878 4098.93 6 5 2285.6 1 0 BHIM refund merchant null Delhi Pune 0 2 650 1488 449 4736.51 13 5 3115.9 1 0 GPay request individual null Bangalore Ahmedabad 0 3 148 151 32 1267.2 20 5 1045.2799 0 0 BHIM refund merchant null Ahmedabad Chennai 0 4 508 836 786 1579.66 18 5 1371.0801 0 0 PhonePe request biller null Jaipur Jaipur 0 12 20 24 363 3962.17 6 5 2238.94 1 0 Paytm pay individual null Jaipur Pune 0 14 1535 812 368 2492.52 20 5 1803.37 0 0 GPay refund biller null Chennai Delhi 0 16 695 1003 682 4538.94 22 5 2935.27 1 0 Paytm request individual null Ahmedabad Mumbai 0 20 906 751 510 1665.24 17 5 131.17993 0 0 BHIM request individual null Ahmedabad Ahmedabad 0 21 916 1073 731 1176.64 20 5 713.04004 0 0 PhonePe refund biller null Bangalore Delhi 0 26 1794 1345 744 313.52 20 5 50.97998 0 0 BHIM refund individual null Ahmedabad Delhi 0 29 1839 1272 251 2553.99 11 5 1158.39 0 0 PhonePe refund merchant null Jaipur Bangalore 0 32 1194 59 245 4101.61 16 5 3674.71 1 0 BHIM request biller null Ahmedabad Bangalore 0 33 78 154 819 1822.89 10 5 688.88 0 0 GPay pay individual null Chennai Chennai 0 35 1300 1016 275 2424.22 5 5 634.13 0 1 GPay refund biller null Bangalore Hyderabad 0 36 1248 687 830 1203.33 6 5 210.94995 0 0 PhonePe refund individual null Bangalore Chennai 0 38 621 1350 487 1602.65 11 5 -290.27002 0 0 GPay pay merchant null Kolkata Pune 0 40 574 612 808 249.35 4 5 -991.25 0 1 Paytm refund individual null Pune Jaipur 0 41 42 778 395 3889.28 21 5 2618.75 1 0 PhonePe pay individual null Chennai Ahmedabad 0 42 1251 1205 486 3694.83 3 5 2364.96 1 1 Paytm request biller null Pune Hyderabad 0 43 256 878 221 4572.29 11 5 3273.07 1 0 Paytm pay individual null Hyderabad Chennai 0 44 704 973 393 861.47 14 5 -734.22 0 0 Paytm refund merchant null Hyderabad Delhi 0 46 964 1369 869 1754.78 9 5 967.52 0 0 BHIM pay biller null Kolkata Pune 0 49 516 549 950 2909.21 5 5 1080.84 0 1 GPay request biller null Hyderabad Bangalore 0 54 964 799 869 1390.25 9 5 602.99 0 0 Paytm refund biller null Kolkata Pune 0 57 323 859 521 2619.39 8 5 2108.7798 0 0 Paytm refund merchant null Bangalore Delhi 0 58 1512 559 720 4039.84 3 5 3133.73 1 1 Paytm pay biller null Jaipur Pune 0 59 1274 782 952 4103.05 9 5 3578.2698 1 0 Paytm request individual null Mumbai Mumbai 0 60 729 988 361 85.99 13 5 -619.81 0 0 Paytm request individual null Kolkata Jaipur 0 75 979 522 238 443.15 17 5 -198.30002 0 0 PhonePe request individual null Jaipur Chennai 0 76 906 751 510 3947.78 18 5 2413.72 1 0 Paytm pay individual null Ahmedabad Kolkata 0 77 1041 718 19 4536.87 21 5 2570.7803 1 0 GPay pay individual null Jaipur Delhi 0 78 1111 1408 589 345.67 15 5 28.74002 0 0 Paytm pay individual null Bangalore Kolkata 0 80 698 945 520 3886.12 20 5 2211.69 1 0 BHIM pay merchant null Pune Jaipur 0 81 1102 276 278 2177.61 1 5 668.0001 0 1 GPay pay merchant null Mumbai Bangalore 0 83 280 1190 342 3888.53 3 5 3607.34 1 1 PhonePe pay individual null Kolkata Chennai 0 90 953 361 672 4596.12 16 5 4457.27 1 0 GPay request merchant null Hyderabad Jaipur 0 94 1994 1076 146 4160.9 15 5 2608.7598 1 0 BHIM pay individual null Hyderabad Bangalore 0 95 1934 416 473 2923.46 11 5 2518.1099 0 0 PhonePe pay biller null Hyderabad Bangalore 0 97 538 1319 490 3846.99 2 5 2457.1 1 1 Paytm refund biller null Jaipur Bangalore 0 98 1714 467 858 4610.36 9 5 4184.1597 1 0 PhonePe refund merchant null Kolkata Hyderabad 0 99 415 1467 478 4490.4 3 5 3745.19 1 1 Paytm pay biller null Mumbai Kolkata 0 102 449 268 477 1220.95 7 5 -18.140015 0 0 GPay pay individual null Hyderabad Jaipur 0 104 1850 1055 508 4645.61 22 5 3984.8198 1 0 BHIM pay merchant null Pune Jaipur 0 107 188 380 85 324.28 20 5 -1374.1699 0 0 BHIM pay individual null Chennai Pune